In [1]:
pip install -r requirements.txt

In [2]:
import glob
import numpy as np
from tqdm import tqdm
import torch
import torch.nn as nn
import torch.nn.functional as F
import pretty_midi
import pypianoroll
from torch.utils.data import DataLoader, TensorDataset

In [3]:
# Get list of MIDI files from your dataset folder
midi_files = glob.glob('./dataset/*.mid')
print("MIDI files found:", len(midi_files))

piano_tracks = []
fixed_length = 500  # e.g., fixed number of time steps for training

for f in tqdm(midi_files):
    try:
        # Try to load using pypianoroll's loader (which handles type 1 files)
        multitrack = pypianoroll.load(f)
    except Exception as e:
        print(f"Error loading {f} with pypianoroll: {e}")
        continue
    
    for track in multitrack.tracks:
        # Filter out tracks with no notes
        if track.pianoroll.sum() == 0:
            continue
        pr = track.pianoroll
        # Truncate or pad the piano roll to fixed_length along time axis
        if pr.shape[1] < fixed_length:
            pr = np.pad(pr, ((0, 0), (0, fixed_length - pr.shape[1])), mode='constant')
        else:
            pr = pr[:, :fixed_length]
        # Add channel dimension if needed (e.g., for CNN input)
        pr = np.expand_dims(pr, axis=0)
        piano_tracks.append({'pianoroll': pr, 'is_drum': track.is_drum, 'name': track.name})
    
    # Optional: print debugging information for this file
    print(multitrack)
    for i, track in enumerate(multitrack.tracks):
        print(f"Track {i} ({track.name}): sum = {track.pianoroll.sum()}")

print("Total instrument tracks processed:", len(piano_tracks))


MIDI files found: 21307


  0%|          | 9/21307 [00:00<04:14, 83.71it/s]

Error loading ./dataset\001-v1.mid with pypianoroll: This file contains pickled (object) data. If you trust the file you can load it unsafely using the `allow_pickle=` keyword argument or `pickle.load()`.
Error loading ./dataset\001-v2.mid with pypianoroll: This file contains pickled (object) data. If you trust the file you can load it unsafely using the `allow_pickle=` keyword argument or `pickle.load()`.
Error loading ./dataset\001-v3.mid with pypianoroll: This file contains pickled (object) data. If you trust the file you can load it unsafely using the `allow_pickle=` keyword argument or `pickle.load()`.
Error loading ./dataset\001.mid with pypianoroll: This file contains pickled (object) data. If you trust the file you can load it unsafely using the `allow_pickle=` keyword argument or `pickle.load()`.
Error loading ./dataset\002-v1.mid with pypianoroll: This file contains pickled (object) data. If you trust the file you can load it unsafely using the `allow_pickle=` keyword argumen

  0%|          | 27/21307 [00:00<04:00, 88.46it/s]

Error loading ./dataset\006-v1.mid with pypianoroll: This file contains pickled (object) data. If you trust the file you can load it unsafely using the `allow_pickle=` keyword argument or `pickle.load()`.
Error loading ./dataset\006.mid with pypianoroll: This file contains pickled (object) data. If you trust the file you can load it unsafely using the `allow_pickle=` keyword argument or `pickle.load()`.
Error loading ./dataset\007-v1.mid with pypianoroll: This file contains pickled (object) data. If you trust the file you can load it unsafely using the `allow_pickle=` keyword argument or `pickle.load()`.
Error loading ./dataset\007.mid with pypianoroll: This file contains pickled (object) data. If you trust the file you can load it unsafely using the `allow_pickle=` keyword argument or `pickle.load()`.
Error loading ./dataset\008-v1.mid with pypianoroll: This file contains pickled (object) data. If you trust the file you can load it unsafely using the `allow_pickle=` keyword argument o

...

Error loading ./dataset\You_Could_Be_Mine.1.mid with pypianoroll: This file contains pickled (object) data. If you trust the file you can load it unsafely using the `allow_pickle=` keyword argument or `pickle.load()`.
Error loading ./dataset\You_Could_Be_Mine.mid with pypianoroll: This file contains pickled (object) data. If you trust the file you can load it unsafely using the `allow_pickle=` keyword argument or `pickle.load()`.
Error loading ./dataset\You_Didn_t_Have_to_Be_So_Nice.mid with pypianoroll: This file contains pickled (object) data. If you trust the file you can load it unsafely using the `allow_pickle=` keyword argument or `pickle.load()`.
Error loading ./dataset\You_Dont_Bring_Me_Flowers.mid with pypianoroll: This file contains pickled (object) data. If you trust the file you can load it unsafely using the `allow_pickle=` keyword argument or `pickle.load()`.
Error loading ./dataset\You_Dont_Fool_Me.1.mid with pypianoroll: This file contains pickled (object) data. If you 

 99%|█████████▉| 21184/21307 [03:12<00:01, 86.30it/s]

Error loading ./dataset\You_Give_Love_a_Bad_Name.1.mid with pypianoroll: This file contains pickled (object) data. If you trust the file you can load it unsafely using the `allow_pickle=` keyword argument or `pickle.load()`.
Error loading ./dataset\You_Give_Love_a_Bad_Name.2.mid with pypianoroll: This file contains pickled (object) data. If you trust the file you can load it unsafely using the `allow_pickle=` keyword argument or `pickle.load()`.
Error loading ./dataset\You_Give_Love_a_Bad_Name.3.mid with pypianoroll: This file contains pickled (object) data. If you trust the file you can load it unsafely using the `allow_pickle=` keyword argument or `pickle.load()`.
Error loading ./dataset\You_Give_Love_a_Bad_Name.4.mid with pypianoroll: This file contains pickled (object) data. If you trust the file you can load it unsafely using the `allow_pickle=` keyword argument or `pickle.load()`.
Error loading ./dataset\You_Give_Love_a_Bad_Name.5.mid with pypianoroll: This file contains pickled 

100%|██████████| 21307/21307 [03:13<00:00, 110.33it/s]

Error loading ./dataset\You_Got_It.mid with pypianoroll: This file contains pickled (object) data. If you trust the file you can load it unsafely using the `allow_pickle=` keyword argument or `pickle.load()`.
Error loading ./dataset\You_Got_It_The_Right_Stuff_.1.mid with pypianoroll: This file contains pickled (object) data. If you trust the file you can load it unsafely using the `allow_pickle=` keyword argument or `pickle.load()`.
Error loading ./dataset\You_Got_It_The_Right_Stuff_.mid with pypianoroll: This file contains pickled (object) data. If you trust the file you can load it unsafely using the `allow_pickle=` keyword argument or `pickle.load()`.
Error loading ./dataset\You_Got_Lucky.1.mid with pypianoroll: This file contains pickled (object) data. If you trust the file you can load it unsafely using the `allow_pickle=` keyword argument or `pickle.load()`.
Error loading ./dataset\You_Got_Lucky.mid with pypianoroll: This file contains pickled (object) data. If you trust the file